# Home Work -- Optimization Algorithms

**Author**: Jayanth Anantha Raman

## Problem Statement -- Coding Task
Previously, you did the following. In the "linear model" notebook, you replaced the linear function with a quadratic function $\alpha + \beta x + \gamma x^2$. The suggested value of $\gamma_\text{true}$ was 8.0.  Use your final notebook as a starting point.
 1. Implement the following optimizers:
    1. Gradient descent (already finished)
    1. Gradient descent with momentum
    1. Gradient descent with Nesterov momentum
    1. AdaGrad
    1. Adam

and check what mean-squared-error you get after the notebook completes its optimizer iterations.

 2. Replace $\alpha + \beta x + \gamma x^2$ with $\alpha + \beta x + 10^{-10} \, \gamma x^2$ and simultaneously make the value of $\gamma_\text{true}$ $10^{10}$ times larger than previously. Then check again the performance of 
    1. Gradient descent (already finished)
    1. Gradient descent with momentum
    1. Gradient descent with Nesterov momentum
    1. AdaGrad
    1. Adam

as in step 2.

 3. Write a short summary of your results (ideally in the PDF format).  Do they correspond to what you expected based on your intuition about the optimizers?

In any of the above please feel free to change the number of data points from 30 to any larger number.

### Imports

In [1]:
import bokeh
import bokeh.plotting as bkp
import functools
import IPython.display as ipydisp
import numpy as np
import time
#
bkp.reset_output()
bkp.output_notebook()
np.set_printoptions(edgeitems=3, precision=4, suppress=True)
PALETTE = bokeh.palettes.Category10_10

Loading BokehJS ...

# Setup -- Polynomial Function and Helper Functions
In this section, we define polynomial function which takes as arguments an array of weights and an input array to generate the output.  It also accepts an optional `factors` array to implement the solution to question #3.

The polynomial function supports a polynomial function of any (integral) degree.

We also define a single training function that is used throughout this notebook.  It takes an update function as an argument to which we pass the implementation of the desired algorithm.  It is also generalized to handle different loss functions and gradients.

Several helper functions are defined.  In all, the functions defined in this section are:
 * `polynomial_function`: generate output for a polynomial of any degree.
 * `train`: generalized training function.
 * `mse_loss`: mean-squared error (MSE) loss function.
 * `gradient_mse`: gradient of the MSE loss.
 * `gen_training_data`: utility to generate training data.
 * `display_losses`: helper function to graph the loss trajectories.
 * `display_fit`: helper function to graph the model fit and compare it to the training data.

## Polynomial Function
We define `polynomial_function` which generates the output for a polynomial of _any_ order.  It takes as input an array of weights and the input, `x`.  A function to test the polynomial is also included.

In [2]:
# Function to generate `y` given `x` and a set of weights.
def polynomial_function(weights, x, factors=None):
    '''
    weights (numpy.array) = [a0, a1, a2, ...]
    x (numpy.array)
    factors (numpy.array) = [k0, k1, k2, ...]
    output (numpy.array) = k0 * a0 + k1 * a1 * x + k2 * a2 * x ** 2 + ...
    '''
    if isinstance(x, list):
        x = np.array(x)
    if factors is not None:
        weights = weights * factors
    out = weights[0]
    xn = x
    for w in weights[1:]:
        out = out + w * xn
        xn = xn * x
    return out

def test_polynomial_function():
    x1 = 3.1415
    tmp1 = 4 + 3.2 * x1 + 2.1 * x1 * x1 + 8.53 * x1 * x1 * x1
    assert polynomial_function([6.24, 4.14], x1) == 6.24 + 4.14 * x1
    assert polynomial_function([4, 3.2, 2.1, 8.53], x1) == tmp1
    assert all(polynomial_function([4, 3.2, 2.1, 8.53], [x1, x1]) == np.array([tmp1, tmp1]))
test_polynomial_function()

## Training Data Generation
We define a utility function to help with the generation of training data.  Gaussian noise with the specified variance is added to the output.  For reproducibility, it seeds the random number generator.

In [3]:
def gen_training_data(wt_true, npoints=50, gauss_noise_sd=0.4, seed=414243,
                     fit_func=polynomial_function):
    '''Generate (simulate) training data'''
    np.random.seed(seed)
    xtrain = np.random.random(npoints)
    ytrain = fit_func(wt_true, xtrain) + gauss_noise_sd * np.random.randn(npoints)
    return xtrain, ytrain

## MSE Loss Criterion
The mean-squared error loss, $L_\text{MSE}$, is defined as:
$$
L_\text{MSE} = \frac{1}{M} \sum_{i=1}^{M} \left( y_i - \hat{y}_i \right)^2
$$
where
$$
\begin{align}
y_i &= \text{sample of the actual output (from training data)}, \\
\hat{y}_i &= \text{corresponding model fit}, \\
M &= \text{number of samples}.
\end{align}
$$

We implement the MSE Loss in the function below.

In [4]:
def mse_loss(y, ypred):
    return np.mean((y - ypred) ** 2)

## Gradient Function (MSE Loss)
Next, we define a function to compute the gradient.  Here we assume an L2 loss or a mean-squared error (MSE) loss.

The gradient forms a building block for the various optimizers implemented and discussed in this notebook.

A polynomial model, $\hat{y}$, for the $i$th input sample $x_i$, is defined as
$$
\hat{y}_i = w_0 + w_1 x_i + w_2 x_i^2 + ... = \sum_{j=0} w_{j} x_i^{j}
$$

The gradient estimate, $\hat{\mathbf{g}}$, is defined as
$$
\hat{\mathbf{g}} = \nabla L = \left( \frac{\partial L}{\partial w_0}, \frac{\partial L}{\partial w_1}, ... \right)
$$

For the polynomial fit,
$$
\frac{\partial \hat{y}_i}{\partial w_j} = x_i^{j} \quad j=0, 1, ...
$$

If $L_i$ is the loss for the $i$th sample, then
$$
L_\text{MSE} = \frac{1}{M} \sum_{i=1}^{M} L_i
$$

And, hence
$$
\begin{align}
\frac{\partial L_i}{\partial w_j} &= \frac{\partial L}{\partial \hat{y}_i} 
                                     \frac{\partial \hat{y}_i}{\partial w_j} \\
    &= 2 x_i^{j} \left( \hat{y}_i - y_i \right) \quad j=0, 1, ... \\
    &= 
\begin{cases}
x_i \frac{\partial L_i}{\partial w_{j - 1}} & j=1, ... \\
2 \left( \hat{y}_i - y_i \right) & j=0
\end{cases}
\end{align}
$$

Hence, the next component of the gradient can be computed from the previous component by multiplying with $x$.

If any of the weights has an additional factor--e.g. the $10^{-10}$ factor--then that factor simply multiplies the gradient component for that weight.

The implementation is below.

In [5]:
def gradient_mse(x, y, ypred, nweights, factors=None):
    '''
    x (numpy array) = input
    y (numpy array) = (true) output
    ypred (numpy ndarray) = predicted output
    nweights (int) = polynomial order + 1 = len(weights)
    factors (array) = must have length of nweights
    '''
    gradient = []
    if factors is None:
        factors = [1] * nweights
    derivative_of_loss = 2 * (ypred - y)
    gradient.append(factors[0] * derivative_of_loss.mean())
    for ii in range(1, nweights):
        derivative_of_loss = x * derivative_of_loss
        gradient.append(factors[ii] * derivative_of_loss.mean())
    return np.array(gradient)
# test
x1, y1 = gen_training_data([1, 3, 8])
out = gradient_mse(x1, y1, y1 + 1, 3)
print(out)
x1, y1 = gen_training_data([1, 3, 8 * 1e+10])
out = gradient_mse(x1, y1, y1 + 1, 3, factors=[1, 1, 1e-10])
print(out)

[2.     1.0424 0.7259]
[2.     1.0424 0.    ]


## Training Function
We define a common function for the model training for all of the optimization algorithms.  The optimization algorithm is passed as the input parameter `update_func` which updates the weights based on the optimization algorithm.  It has the signature:
```
update_func(weights, x, y, learning_rate, state)
```
The weights are updated in-place.

`update_func` returns an updated state which then needs to be passed back to it on the next call.  The `state` parameter is initialized to `None` on the first call of `update_func`.  Any additional parameters to `update_func` needs to be handled via partial functions (`functools.partial`).

In [6]:
# Train
print_line = lambda i, l, g: f'{i:5d}: {l:11.8f}  {g:9.6f} '
def train(xtrain, ytrain, nweights, update_func, niter, learning_rate=0.2,
          fit_func=polynomial_function, loss_func=None, grad_func=gradient_mse,
          init_weights=None, sample_iter=1, print_iter=10,
          print_state=True, rseed=4243):
    '''
    Main training function to train a polynomial of any degree.
    xtrain (array) = training data, x
    ytrain (array) = training data, y
    nweights (int) = number of weights = polynomial_degree + 1
    update_func (function) = function to update the weights.  Returns the state
        and the gradient.  API: update_func(weights, x, y, lr, state).
    niter (int) = number of iterations to run
    learning_rate (float)
    fit_func (function) = function to generate y from x, y = fit_func(weights, xtrain).
        Use functools.partial to handle additional parameters.
    loss_func (function) = loss function with api loss_func(ypred, ytrain)
        If given, used for printing the progress of the algorithm and
        to return the loss trajectory.
    grad_func (function) = gradient function, used to compute the initial gradient only.
        It is not passed to the update_func (separately functools.partial that).
    init_weights (array) = initial weights.  Randomized by default.
    sample_iter (int) = frequency of iterations to sample the loss function.
    print_iter (int) = frequency to print the progress.
    print_state (bool) = whether to print the state info or not, during progress.
    rseed = seed for random number generator, for reproducibility.  Pass None to
        seed from clock.  See numpy.random.RandomState.
    '''
    # initialize weights
    t0 = time.perf_counter()
    weights = init_weights
    if not weights:
        if rseed is not None:
            np.random.seed(rseed)
        weights = np.random.randn(nweights) / nweights
    # Print parameters
    print(f'Learning rate={learning_rate}, Number of weights={nweights}')
    fname = getattr(update_func, '__name__', getattr(update_func, 'func', object).__name__)
    print(f'Weight-update function={fname}')
    print('Initial weights:', ', '.join(f'{w:.16f}' for w in weights))
    # Run Header
    print(f'{"Iter":>5s}  {"Loss":>11s}  {"Gradient":>9s}  Weights')
    ypred = fit_func(weights, xtrain)
    l = loss_func(ypred, ytrain)
    g = np.sqrt(np.sum(grad_func(xtrain, ytrain, ypred, nweights) ** 2))
    print(print_line(0, l, g), weights)
    loss_values = []
    state = None
    for ii in range(niter):
        state, grad = update_func(weights, xtrain, ytrain, learning_rate, state=state)
        # print(grad)
        if loss_func and (ii + 1) % sample_iter == 0:
            loss_values.append(loss_func(fit_func(weights, xtrain), ytrain))
        if loss_func and (ii + 1) % print_iter == 0:
            l = loss_func(fit_func(weights, xtrain), ytrain)
            g = np.sqrt(np.sum(grad ** 2))
            print(print_line(ii + 1, l, g), weights)
            if print_state and state is not None:
                print('    ', end='')
                for k, v in state.items():
                    print(f'{k}: {v}', end='; ')
                print()
    avgloss = np.mean(loss_values[-10:])
    print(f'Loss values: Last: {loss_values[-1]:.6f}, Average (last 10): {avgloss:.6f}')
    print(f'Total time: {time.perf_counter() - t0:.2f} sec')
    return weights, np.array(loss_values)

## Helper Functions

Helper functions--one to display losses, another to display the fit compared to the training data, and another to display both losses and fit as subplots. 

In [7]:
# Helper function to display results
def display_losses(losses, width=600, height=400, colors=PALETTE, title='Loss',
                   labels=None, lw=2):
    '''
    losses = list of losses, each loss is an array
    '''
    # @todo: if axis_type can be set a posteriori, then fig can be a param
    fig = bkp.figure(width=width, height=height, x_axis_type='log')
    fig.title = bokeh.models.annotations.Title(text=title)
    if not labels:
        labels = [''] * len(losses)
    for loss, color, lbl in zip(losses, colors, labels):
        fig.line(range(1, len(loss) + 1), loss, line_color=color,
                 line_width=lw, legend_label=lbl)
    fig.xaxis.axis_label = 'log(iteration number)'
    fig.yaxis.axis_label = 'Loss'
    return fig

def display_poly_fit(xt, yt, wt_true, wt_preds=None, colors=PALETTE, title='Model Fit',
                     width=600, height=400, labels=None, fit_func=polynomial_function):
    '''
    wt_preds = list of arrays, each array is a weight array
    colors = list of colors, can be longer than wt_preds
    '''
    s1 = bkp.figure(width=width, height=height, title=title)
    s1.circle(xt, yt, radius=0.01, color=PALETTE[9])
    x = np.linspace(0.0, 1.0)
    ytrue = fit_func(wt_true, x)
    s1.line(x, ytrue, line_color='gray', line_dash='dashed', line_width=2,
            legend_label='Actual')
    if wt_preds:
        if not labels:
            if len(wt_preds) > 1:
                labels = [f'Fit {i}' for i in range(len(wt_preds))]
            else:
                labels = ['Fit']
        for wt, col, label in zip(wt_preds, colors, labels):
            ypred = fit_func(wt, x)
            s1.line(x, ypred, line_color=col, line_width=2, legend_label=label)
    s1.legend.location = 'bottom_right'
    s1.xaxis.axis_label = 'x'
    s1.yaxis.axis_label = 'y'
    return s1

def display_results(xt, yt, wt_true, wt_preds, losses, colors=PALETTE, labels=None):
    '''
    Display both fit and losses as two subplots.
    By default, colors starts at PALETTE[1:]
    '''
    s1 = display_poly_fit(xt, yt, wt_true, wt_preds, colors=colors,
                         width=400, height=300, labels=labels)
    #
    s2 = display_losses(losses, width=400, height=300, colors=colors, labels=labels)
    p = bokeh.layouts.row(s1, s2)
    bkp.show(p)

# Training Data

In [8]:
wt_true = [1.0, 2.0, 8.0]
xtrain, ytrain = gen_training_data(wt_true, seed=200127)
bkp.show(display_poly_fit(xtrain, ytrain, wt_true, title='Training Data'))

# Gradient Descent -- Basic
We follow the notation of the 2016 book [_Deep Learning_](http://www.deeplearningbook.org),
by Goodfellow et. al.

The update for the basic gradient descent algorithm is:
$$
\boldsymbol{\theta}_t \leftarrow \boldsymbol{\theta}_{t-1} - \epsilon \, \mathbf{\hat{g}}(\boldsymbol{\theta}_{t-1})
$$
where,
$$
\begin{align}
\boldsymbol{\theta}_t &= \text{the parameter vector updated at time t,}\\
\epsilon &= \text{the learning rate, and}\\
\mathbf{\hat{g}} &= \text{the gradient estimate}.
\end{align}
$$

The learning rate, $\epsilon$, is shown as a constant above.  But it doesn't have to be and can change with time.  Later, we will look into adaptive algorithms that change the learning rate over time.


The update function is defined below.

In [9]:
# Basic gradient descent
def update_gradient_descent_basic(weights, x, y, lr, state,
                                  grad_func=gradient_mse, fit_func=polynomial_function):
    Nweights = len(weights)
    ypred = fit_func(weights, x)
    grad = grad_func(x, y, ypred, Nweights)
    weights[:] = weights - lr * grad
    # there is not state for basic GD, so simply return the input param
    return state, grad

Now, let's train using the basic gradient descent algorithm defined above, and plot the results.

In [10]:
out = train(xtrain, ytrain, len(wt_true), update_gradient_descent_basic,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_gdb, loss_gdb = out
print('Predicted weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_basic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.12614844   0.011150  [0.6148 4.49   5.8669]
 1600:  0.11954696   0.007172  [0.7003 3.9806 6.37  ]
 2400:  0.11681571   0.004613  [0.7552 3.653  6.6936]
 3200:  0.11568572   0.002967  [0.7906 3.4423 6.9018]
 4000:  0.11521820   0.001909  [0.8133 3.3068 7.0357]
 4800:  0.11502477   0.001228  [0.8279 3.2196 7.1218]
 5600:  0.11494475   0.000790  [0.8373 3.1635 7.1772]
 6400:  0.11491164   0.000508  [0.8434 3.1274 7.2129]
 7200:  0.11489794   0.000327  [0.8473 3.1042 7.2358]
 8000:  0.11489227   0.000210  [0.8498 3.0893 7.2505]
 8800:  0.11488993   0.000135  [0.8514 3.0797 7.26  ]
 9600:  0.11488896   0.000087  [0.8524 3.0735 7.2661]
10400:  0.11488856   0.000056  [0.8531 3.0696 7.27  ]
11200:  0.11488839   0.000036  [0

In [11]:
tol = 1e-9
np.argmax(np.isclose(loss_gdb, loss_gdb[-1], rtol=0, atol=tol))

15511

In [12]:
display_results(xtrain, ytrain, wt_true, wt_preds=[wt_gdb], losses=[loss_gdb])

For the chosen learning rate, the left graph tells us that we get a pretty good fit for the data.

In order to get a quantitative measure of the fit, let's compute the $R^2$ measure which is defined as
$$
\begin{align}
R^2 &= 1 - \frac{\sum \left( y_i - \hat{y}_i \right)^2}{\sum \left( y_i - \bar{y} \right)^2} \\
    &= 1 - \frac{M L_\text{MSE}}{\sum \left( y_i - \bar{y} \right)^2}
\end{align}
$$
where $\bar{y}$ is the mean value of $y$.

Usually $0 \le R^2 \le 1$, although other values are possible.  There is also an adjusted-$R^2$ measure which takes into account the number of parameters of the model.  But we will not use that since we are keeping the number of parameters constant.

The higher the $R^2$, the better.  If we had no other information, we could simply use the mean of $y$ as its predictor.  The $R^2$ measure compares a model's prediction to the mean-as-a-predictor model.  If we are doing no better than the mean, we would get an $R^2$ of zero.  And with a perfect prediction, i.e. $\hat{y} = y$, we would get an $R^2$ of one.

More information can be found in this [wikipedia article](https://en.wikipedia.org/wiki/Coefficient_of_determination).

We define the $R^2$ function below.

In [13]:
def Rsquared(yt, mse):
    M = len(yt)
    return 1.0 - M * mse / np.sum((yt - np.mean(yt)) ** 2)

And compute it for the MSE we obtained for the basic gradient descent algorithm.

In [14]:
R2_gdb = Rsquared(ytrain, loss_gdb[-1])
print(R2_gdb)

0.9875771317701262


We get a value close to one.

In [15]:
# Convergence
tol=1e-9
np.argmax(np.isclose(loss_gdb, loss_gdb[-1], rtol=0, atol=tol))

15511

## Exploding Gradients
If the learning rate is large, it could lead to exploding gradients as shown below.

The gradient continuously increases as does the loss and the parameter values.  It is a point of no return.

Hence, for the basic gradient descent algorithm, we cannot have learning rates that are too large.

In [16]:
out = train(xtrain, ytrain, len(wt_true), update_gradient_descent_basic,
            niter=800, learning_rate=0.75, loss_func=mse_loss, rseed=200127,
            print_iter=100)

Learning rate=0.75, Number of weights=3
Weight-update function=update_gradient_descent_basic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  100: 12497.00739537  252.104621  [-80.4543 -37.9045 -23.3619]
  200: 7176896.23196317  6041.549326  [-1941.9285 -1012.8597  -693.213 ]
  300: 4121655582.98523903  144782.424448  [-46553.0844 -24365.5335 -16757.2805]
  400: 2367046210359.41357422  3469631.595725  [-1115636.3154  -583991.9241  -401731.4386]
  500: 1359382813368765.00000000  83147823.059205  [-26735631.9322 -13995127.1589  -9627431.5293]
  600: 780686758541092608.00000000  1992592091.910809  [-6.4070e+08 -3.3539e+08 -2.3072e+08]
  700: 448344505291363188736.00000000  47751379394.724136  [-1.5354e+10 -8.0373e+09 -5.5290e+09]
  800: 257482009558609622466560.00000000  1144335683833.955322  [-3.6795e+11 -1.9261e+11 -1.3250e+11]
Loss values: Last: 2574820095586096

# Gradient Descent With Momentum
Like a ball rolling down a hill that gathers momentum, this optimization algorithm is designed to accelerate learning in the optimal directions by accumulating exponentially decaying moving averages of past gradients.

The update for the gradient descent algorithm with momentum is defined as:
$$
\begin{align}
\boldsymbol{\nu}_t & \leftarrow \alpha \boldsymbol{\nu}_{t - 1}
        - \epsilon \, \mathbf{\hat{g}}(\boldsymbol{\theta}_{t - 1}) \\
\boldsymbol{\theta}_t & \leftarrow \boldsymbol{\theta}_t + \boldsymbol{\nu}_t
\end{align}
$$
where,
$$
\begin{align}
\boldsymbol{\nu}_t &= \text{the velocity at time $t$,} \\
\boldsymbol{\theta}_t &= \text{the parameter vector at time $t$,} \\
\epsilon &= \text{the learning rate,} \\
\mathbf{\hat{g}} &= \text{the gradient estimate, and} \\
\alpha &= \text{momentum parameter.}
\end{align}
$$

Accordingly, the update function is defined below.  Note that we maintain the velocity state in the `state` parameter.

In [17]:
def update_gradient_descent_momentum_classic(
    weights, x, y, lr, state=None, momentum=0.0,
    fit_func=polynomial_function, grad_func=gradient_mse):

    if state is None:
        state = {'vel': np.zeros(len(weights))}
    Nweights = len(weights)
    ypred = fit_func(weights, x)
    grad = grad_func(x, y, ypred, Nweights)
    state['vel'] = momentum * state['vel'] - lr * grad
    weights[:] = weights + state['vel']
    return state, grad

## momentum = 0.0 (Classic Algo)
First we'll double check the implementation with `momentum=0.0`.  We keep the same learning rate as the basic gradient descent.  We also initialize the parameters with the same values as before by using the same seed for the random number generator.

This should yield the same result as the basic gradient descent algorithm.

In [18]:
update_func = functools.partial(update_gradient_descent_momentum_classic, momentum=0.0)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom00_cl, loss_mom00_cl = out
print('Predicted weights:', wt_mom00_cl)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.12614844   0.011150  [0.6148 4.49   5.8669]
    vel: [ 0.0001 -0.0008  0.0008]; 
 1600:  0.11954696   0.007172  [0.7003 3.9806 6.37  ]
    vel: [ 0.0001 -0.0005  0.0005]; 
 2400:  0.11681571   0.004613  [0.7552 3.653  6.6936]
    vel: [ 0.0001 -0.0003  0.0003]; 
 3200:  0.11568572   0.002967  [0.7906 3.4423 6.9018]
    vel: [ 0.     -0.0002  0.0002]; 
 4000:  0.11521820   0.001909  [0.8133 3.3068 7.0357]
    vel: [ 0.     -0.0001  0.0001]; 
 4800:  0.11502477   0.001228  [0.8279 3.2196 7.1218]
    vel: [ 0.     -0.0001  0.0001]; 
 5600:  0.11494475   0.000790  [0.8373 3.1635 7.1772]
    vel: [ 0.     -0.0001  0.0001]; 
 6400:  0.11491164   0.000508  [0.8434 3.1274 7.2129]
    vel: [ 0. -0.  0.]; 
 7200:  

And, sure enough, we see the exact same results as with the basic gradient descent algorithm.  The algorithm converges around the 15,000th iteration.

## momentum = 0.5 (Classic Algo)
Now, let's increase momentum to 0.5.  We expect the convergence to be faster.

In [19]:
update_func = functools.partial(update_gradient_descent_momentum_classic, momentum=0.5)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=12000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom50_cl, loss_mom50_cl = out
print('Predicted weights:', wt_mom50_cl)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11954591   0.007175  [0.7003 3.9805 6.3701]
    vel: [ 0.0002 -0.001   0.001 ]; 
 1600:  0.11568359   0.002965  [0.7906 3.4418 6.9023]
    vel: [ 0.0001 -0.0004  0.0004]; 
 2400:  0.11502408   0.001225  [0.828  3.2192 7.1222]
    vel: [ 0.     -0.0002  0.0002]; 
 3200:  0.11491146   0.000506  [0.8434 3.1272 7.2131]
    vel: [ 0.     -0.0001  0.0001]; 
 4000:  0.11489223   0.000209  [0.8498 3.0892 7.2507]
    vel: [ 0. -0.  0.]; 
 4800:  0.11488895   0.000086  [0.8524 3.0735 7.2662]
    vel: [ 0. -0.  0.]; 
 5600:  0.11488839   0.000036  [0.8535 3.067  7.2726]
    vel: [ 0. -0.  0.]; 
 6400:  0.11488829   0.000015  [0.854  3.0643 7.2752]
    vel: [ 0. -0.  0.]; 
 7200:  0.11488828   0.000006  [0.8541 3.063

Indeed, we see that the loss converges faster--around the 8,000th iteration compared to around the 15,000th iteration with no momentum.

Moreover, notice that the values of the weights for some iteration here are comparable to a later iteration with `momentum=0.0`.  For example, with `momentum=0.50`, in the 3,000th iteration, the weights are:
```
3000:  0.11492435, [0.8407 3.1432 7.1973]
```
And, with `momentum=0.00`, we find virtually identical weights in the 6,000th iteration:
```
6000:  0.11492460, [0.8407 3.1435 7.197 ]
```
That is, virtually the same loss and weight values, but at a later iteration.

This matches our intuition that, for this simple example, and with the same initialization and learning rate, the path traversed with `momentum=0.00` and `momentum=0.50` are the same except that the latter traverses it faster.

## momentum = 0.9 (Classic Algo)
Now, let's increase the momentum coefficient to 0.9.  We expect the convergence to be faster than with `momentum=0.5`.

In [20]:
update_func = functools.partial(update_gradient_descent_momentum_classic, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=8000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom90_cl, loss_mom90_cl = out
print('Predicted weights:', wt_mom90_cl)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11489095   0.000173  [0.8506 3.0844 7.2553]
    vel: [ 0.     -0.0001  0.0001]; 
 1600:  0.11488827   0.000002  [0.8542 3.0626 7.2769]
    vel: [ 0. -0.  0.]; 
 2400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 3200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 4000:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 4800:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 5600:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0. -0.  0.]; 
 6400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 7200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0. -0.  0.]; 
 

Sure enough, with `momentum=0.9`, it converges around the 2,000th iteration itself!

## Comparison of Algorithm With Different Momentum Values

### MSE
The MSE for all three momentum coefficient values are almost identical.  Moreover, they are all close to the MSE for the basic gradient descent algorithm.

### Early Convergence
Let's be more precise on when the algorithm converges for the three values of the momentum coefficient.

In [21]:
tol = 1e-9
mc00 = np.argmax(np.isclose(loss_mom00_cl, loss_mom00_cl[-1], rtol=0, atol=tol))
mc50 = np.argmax(np.isclose(loss_mom50_cl, loss_mom50_cl[-1], rtol=0, atol=tol))
mc90 = np.argmax(np.isclose(loss_mom90_cl, loss_mom90_cl[-1], rtol=0, atol=tol))
print(f'mc00={mc00}, mc50={mc50}, mc90={mc90}')

mc00=15511, mc50=7749, mc90=1476


In [22]:
text = f'''
The convergence of loss to the eight digit is summarized in the table below.

| Momentum | Iteration |            Factor |
|----------|----------:|------------------:|
| 0.00     | {mc00:4d} | {mc00 / mc00:.1f} |
| 0.50     | {mc50:4d} | {mc00 / mc50:.1f} |
| 0.90     | {mc90:4d} | {mc00 / mc90:.1f} |

From the table it is clear that `momentum=0.9` converges in about one-tenth
of the iterations compared to no momentum.  And `momentum=0.5` converges
in about half of the iterations.  The ratios hold true for different values
of the learning rate.
'''
# print(text)
ipydisp.display(ipydisp.Markdown(text))


The convergence of loss to the eight digit is summarized in the table below.

| Momentum | Iteration |            Factor |
|----------|----------:|------------------:|
| 0.00     | 15511 | 1.0 |
| 0.50     | 7749 | 2.0 |
| 0.90     | 1476 | 10.5 |

From the table it is clear that `momentum=0.9` converges in about one-tenth
of the iterations compared to no momentum.  And `momentum=0.5` converges
in about half of the iterations.  The ratios hold true for different values
of the learning rate.


### Loss Trajectory
Below, we plot the loss as the gradient descent progresses.

In [23]:
labels = [f'momentum = {m:.2f}' for m in [0.0, 0.5, 0.9]]
p = display_losses([loss_mom00_cl, loss_mom50_cl, loss_mom90_cl],
                  title='Loss for Momentum Algo (Classic)', labels=labels)
# _ = p.circle(t, loss_c90, size=3, legend_label='momentum = 0.9', color='darkgreen')
bkp.show(p)

### More Oscillations With Larger Momentum
While it is clear from that graph that higher momentum values result in faster convergence, the same is not so clear from the graph.

What we do see in the graph is that the speed in convergence seems to come at a cost--there are more oscillations with larger values of the momentum coefficient!

Can the oscillations be reduced or elimated?

For `momentum=0.9`, let us attempt by decreasing the learning rate.

**learning_rate = 0.01**

Let us train with a learning rate of 0.01.

In [24]:
update_func = functools.partial(update_gradient_descent_momentum_classic, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.01, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom01_cl, loss_mom01_cl = out
print('Predicted weights:', wt_mom01_cl)
print('True weights:', wt_true)

Learning rate=0.01, Number of weights=3
Weight-update function=update_gradient_descent_momentum_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.12621206   0.011181  [0.6141 4.494  5.8629]
    vel: [ 0.0001 -0.0008  0.0008]; 
 1600:  0.11955258   0.007176  [0.7002 3.9812 6.3695]
    vel: [ 0.0001 -0.0005  0.0005]; 
 2400:  0.11680952   0.004606  [0.7554 3.6521 6.6946]
    vel: [ 0.0001 -0.0003  0.0003]; 
 3200:  0.11567964   0.002956  [0.7908 3.4409 6.9032]
    vel: [ 0.     -0.0002  0.0002]; 
 4000:  0.11521424   0.001897  [0.8135 3.3053 7.0372]
    vel: [ 0.     -0.0001  0.0001]; 
 4800:  0.11502254   0.001218  [0.8281 3.2183 7.1231]
    vel: [ 0.     -0.0001  0.0001]; 
 5600:  0.11494358   0.000781  [0.8375 3.1625 7.1783]
    vel: [ 0.     -0.0001  0.0001]; 
 6400:  0.11491105   0.000502  [0.8435 3.1266 7.2137]
    vel: [ 0. -0.  0.]; 
 7200: 

In [25]:
labels = ['momentum = 0.01']
display_results(xtrain, ytrain, wt_true, [wt_mom01_cl], [loss_mom01_cl], labels=labels)

Indeed, we notice that the oscillations have decreased.  If we decrease the learning rate even more, we would obtain a smoother curve.

But the time (i.e. iteration) to convergence has increased!

Hence, it appears we have a tradeoff here that if we reduce the learning rate, we do reduce the oscillations.  But that comes at the cost of later convergence.

### Weight Estimates

In [26]:
text = f'''
For completeness, the resulting weight estimates for the three momentum
coefficient values are shown below.

| Momentum | Weights |
|---------:|--------------:|
| true     | {wt_true}     |
| 0.00     | {wt_mom00_cl} |
| 0.50     | {wt_mom50_cl} |
| 0.90     | {wt_mom90_cl} |

The predicted functions are plotted below.
'''
# print(text)
ipydisp.display(ipydisp.Markdown(text))

labels = [f'momentum = {m:.2f}' for m in [0.0, 0.5, 0.9]]
p = display_poly_fit(xtrain, ytrain, wt_true,
                     wt_preds=[wt_mom00_cl, wt_mom50_cl, wt_mom90_cl],
                     labels=labels,
                     title='Model Fit -- Momentum Classic Impl')
bkp.show(p)


For completeness, the resulting weight estimates for the three momentum
coefficient values are shown below.

| Momentum | Weights |
|---------:|--------------:|
| true     | [1.0, 2.0, 8.0]     |
| 0.00     | [0.8543 3.0624 7.2771] |
| 0.50     | [0.8543 3.0624 7.2771] |
| 0.90     | [0.8543 3.0624 7.2771] |

The predicted functions are plotted below.


## Exploding Gradient
Gradient Descent with Momentum also suffers from instability if the learning rate is too large.  An example is shown below.

In [27]:
# Exploding Gradient
update_func = functools.partial(update_gradient_descent_momentum_classic, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=16, learning_rate=1.6, loss_func=mse_loss, rseed=200127,
            print_iter=2)

Learning rate=1.6, Number of weights=3
Weight-update function=update_gradient_descent_momentum_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
    2: 1135.64917878  36.234545  [-23.9887  -7.518   -3.6025]
    vel: [-37.7174 -16.6135 -10.3381]; 
    4: 18350.42448573  158.459531  [-100.4042  -43.4581  -26.7691]
    vel: [-148.4304  -76.4047  -52.0068]; 
    6: 283403.48848535  625.368322  [-386.6154 -195.942  -132.1957]
    vel: [-579.5586 -305.4529 -210.622 ]; 
    8: 4367490.35627497  2455.519875  [-1513.1575  -790.3215  -542.1968]
    vel: [-2279.0425 -1195.0638  -822.5663]; 
   10: 67298642.63913465  9639.081726  [-5946.4595 -3111.1364 -2138.3268]
    vel: [-8951.6485 -4685.2195 -3222.5956]; 
   12: 1036998159.61693943  37837.441777  [-23351.1906 -12218.4685  -8401.8235]
    vel: [-35138.3372 -18391.8486 -12651.1914]; 
   14: 15978997466.89771271  1485

# Gradient Descent with Momentum -- PyTorch Implementation

There is second way to define the gradient-descent-with-momentum algorithm.  This update rule is implemented in pytorch and is slightly different than the one given in the book.  The update for the basic gradient descent algorithm is:
$$
\begin{align}
\boldsymbol{\nu}_t & \leftarrow \alpha \boldsymbol{\nu}_{t - 1} +
    \mathbf{\hat{g}}(\boldsymbol{\theta}_{t - 1}) \\
\boldsymbol{\theta}_t & \leftarrow \boldsymbol{\theta}_{t - 1} - \epsilon \, \boldsymbol{\nu}_t
\end{align}
$$
where,
$$
\begin{align}
\boldsymbol{\nu}_t &= \text{velocity at time $t$,}\\
\boldsymbol{\theta}_t &= \text{the parameter vector at time $t$,} \\
\epsilon &= \text{the learning rate,} \\
\mathbf{\hat{g}} &= \text{the gradient estimate at time $t$, and} \\
\alpha &= \text{momentum parameter.}
\end{align}
$$

Accordingly, we define the update function below.

In [28]:
def update_gradient_descent_momentum_pytorch(weights, x, y, lr, state=None, 
                                             momentum=0.0, fit_func=polynomial_function,
                                             grad_func=gradient_mse):
    if state is None:
        state = {'vel': np.zeros(len(weights))}
    Nweights = len(weights)
    ypred = fit_func(weights, x)
    grad = grad_func(x, y, ypred, Nweights)
    state['vel'] = momentum * state['vel'] + grad
    weights[:] = weights - lr * state['vel']
    return state, grad

## momentum = 0.0 (pytorch impl)
First we'll double check the implementation with `momentum=0.0`.  This should yield the same result as the basic gradient descent algorithm.

In [29]:
update_func = functools.partial(update_gradient_descent_momentum_pytorch, momentum=0.0)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom00_pyt, loss_mom00_pyt = out
print('Predicted weights:', wt_mom00_pyt)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.12614844   0.011150  [0.6148 4.49   5.8669]
    vel: [-0.0013  0.0079 -0.0078]; 
 1600:  0.11954696   0.007172  [0.7003 3.9806 6.37  ]
    vel: [-0.0008  0.0051 -0.005 ]; 
 2400:  0.11681571   0.004613  [0.7552 3.653  6.6936]
    vel: [-0.0005  0.0033 -0.0032]; 
 3200:  0.11568572   0.002967  [0.7906 3.4423 6.9018]
    vel: [-0.0004  0.0021 -0.0021]; 
 4000:  0.11521820   0.001909  [0.8133 3.3068 7.0357]
    vel: [-0.0002  0.0013 -0.0013]; 
 4800:  0.11502477   0.001228  [0.8279 3.2196 7.1218]
    vel: [-0.0001  0.0009 -0.0009]; 
 5600:  0.11494475   0.000790  [0.8373 3.1635 7.1772]
    vel: [-0.0001  0.0006 -0.0006]; 
 6400:  0.11491164   0.000508  [0.8434 3.1274 7.2129]
    vel: [-0.0001  0.0004 -0.0004

We get the exact same run as the basic gradient descent as expected!

## momentum = 0.5 (pytorch impl)
Now, let us increase the momentum coefficient to 0.5.

In [30]:
update_func = functools.partial(update_gradient_descent_momentum_pytorch, momentum=0.5)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=12000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom50_pyt, loss_mom50_pyt = out
print('Predicted weights:', wt_mom50_pyt)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11954591   0.007175  [0.7003 3.9805 6.3701]
    vel: [-0.0017  0.0101 -0.01  ]; 
 1600:  0.11568359   0.002965  [0.7906 3.4418 6.9023]
    vel: [-0.0007  0.0042 -0.0041]; 
 2400:  0.11502408   0.001225  [0.828  3.2192 7.1222]
    vel: [-0.0003  0.0017 -0.0017]; 
 3200:  0.11491146   0.000506  [0.8434 3.1272 7.2131]
    vel: [-0.0001  0.0007 -0.0007]; 
 4000:  0.11489223   0.000209  [0.8498 3.0892 7.2507]
    vel: [-0.      0.0003 -0.0003]; 
 4800:  0.11488895   0.000086  [0.8524 3.0735 7.2662]
    vel: [-0.      0.0001 -0.0001]; 
 5600:  0.11488839   0.000036  [0.8535 3.067  7.2726]
    vel: [-0.      0.0001 -0.    ]; 
 6400:  0.11488829   0.000015  [0.854  3.0643 7.2752]
    vel: [-0.  0. -0.]; 
 7200:  

We see that the loss has converged around the 8,000th iteration with momentum=0.5 compared to the basic gradient descent.  This is the same result as with the classic implementation of momentum.

Also, the results of this implementation are virtually identical to the classic implemetation.  Compare the path of the individual weights as the algorithm run progresses.  The values are identical to the printed precision!  The velocity values are different as is to be expected.

## momentum = 0.9 (pytorch impl)
Now, let's set the momentum coefficient to 0.9.  As always, we keep the other parameters including the initilization to be the same as before.

In [31]:
update_func = functools.partial(update_gradient_descent_momentum_pytorch, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=8000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_mom90_pyt, loss_mom90_pyt = out
print('Predicted weights:', wt_mom90_pyt)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11489095   0.000173  [0.8506 3.0844 7.2553]
    vel: [-0.0002  0.0013 -0.0013]; 
 1600:  0.11488827   0.000002  [0.8542 3.0626 7.2769]
    vel: [-0.  0. -0.]; 
 2400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 3200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 4000:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 4800:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 5600:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0.  0. -0.]; 
 6400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 7200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0.  0. -0.]; 
 

We observe convergence in around the 2,000th iteration itself!

## Comparison
Below, we plot the training loss over time for the three momentum coefficient values.  The graphs are similar to that obtained with the classic implementation above.

In [32]:
labels = [f'momentum = {m:.2f}' for m in [0.0, 0.5, 0.9]]
p = display_losses(losses=[loss_mom00_pyt, loss_mom50_pyt, loss_mom90_pyt],
                   labels=labels,
                   title='Losses -- Momentum Pytorch Impl')
# _ = p.circle(t, loss90, size=3, legend_label='momentum = 0.9', color='lightgreen')
bkp.show(p)

We also show numerically, for this one case, that the two implementations yield the same results.  Shown below are the maximum values of the difference in the losses of the two implementations--and as we can see, the difference is rather insignificant.

In [33]:
print(np.abs(loss_mom50_cl - loss_mom50_pyt).max())
print(np.abs(loss_mom90_cl - loss_mom90_pyt).max())

1.7763568394002505e-15
3.552713678800501e-15


# Gradient descent with Nesterov momentum

As a refinement to the momentum algorithm, the Nesterov momentum algorithm evaluates the gradient after applying the update to the current velocity. Again, there are at least two versions for this algorithm.  As we did previously, we list two variations.

## Classic Version
The update for the gradient descent algorithm with momentum is defined as:
$$
\begin{align}
\boldsymbol{\nu}_t & \leftarrow \alpha \boldsymbol{\nu}_{t - 1}
    - \epsilon \, \mathbf{\hat{g}}(\boldsymbol{\theta}_{t - 1} + \alpha \boldsymbol{\nu}_{t - 1}) \\
\boldsymbol{\theta}_t & \leftarrow \boldsymbol{\theta}_{t - 1} + \boldsymbol{\nu}_t
\end{align}
$$
where,
$$
\begin{align}
\boldsymbol{\nu}_t &= \text{velocity at time $t$,} \\
\boldsymbol{\theta}_t &= \text{the parameter vector at time $t$,} \\
\epsilon &= \text{the learning rate,} \\
\mathbf{\hat{g}} &= \text{the gradient estimate and} \\
\alpha &= \text{momentum parameter.}
\end{align}
$$

## PyTorch Version
The pytorch version is below:
$$
\begin{align}
\boldsymbol{\nu}_t & \leftarrow \alpha \boldsymbol{\nu}_{t - 1} + 
    \mathbf{\hat{g}}\left( \theta_{t - 1} \right) \\
\boldsymbol{\theta}_t & \leftarrow \boldsymbol{\theta}_{t - 1}
    - \epsilon \, \left( \alpha \boldsymbol{\nu}_t + \mathbf{\hat{g}}\left( \theta_{t - 1} \right) \right)
\end{align}
$$


There appears to be a non-trivial difference between the text version and the pytorch version.  In the text version, for the Nesterov momentum, the gradient is computed at $(\boldsymbol{\theta}_{t - 1} + \alpha \boldsymbol{\nu}_{t - 1})$.  In the pytorch version, for both the plain momentum algorithm and the Nesterov momentum, the gradient is computed at $\boldsymbol{\theta}_{t - 1}$.

The update functions are defined below.  As before, we maintain the velocity state in the `state` parameter.

In [34]:
def update_wt_gd_nesterov_classic(weights, x, y, lr, momentum=0.0, state=None,
                                  fit_func=polynomial_function, grad_func=gradient_mse):
    if state is None:
        state = {'vel': np.zeros(len(weights))}
    Nweights = len(weights)
    wt1 = weights + momentum * state['vel']
    ypred = fit_func(wt1, x)
    grad = grad_func(x, y, ypred, Nweights)
    state['vel'] = momentum * state['vel'] - lr * grad
    weights[:] = weights + state['vel']
    return state, grad

def update_wt_gd_nesterov_pytorch(weights, x, y, lr, momentum=0.0, state=None,
                                  fit_func=polynomial_function, grad_func=gradient_mse):
    if state is None:
        state = {'vel': np.zeros(len(weights))}
    Nweights = len(weights)
    ypred = fit_func(weights, x)
    grad = grad_func(x, y, ypred, Nweights)
    state['vel'] = momentum * state['vel'] + grad
    weights[:] = weights - lr * (momentum * state['vel'] + grad)
    return state, grad

## momentum = 0.0
As before, for the algorithm with Nesterov momentum, we run with the momentum coefficient set to zero and compare it to the basic gradient descent algorithm.

In [35]:
# Nesterov (classic)
update_func = functools.partial(update_wt_gd_nesterov_classic, momentum=0.0)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_nest00_cl, loss_nest00_cl = out
print('Predicted weights:', wt_nest00_cl)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_wt_gd_nesterov_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.12614844   0.011150  [0.6148 4.49   5.8669]
    vel: [ 0.0001 -0.0008  0.0008]; 
 1600:  0.11954696   0.007172  [0.7003 3.9806 6.37  ]
    vel: [ 0.0001 -0.0005  0.0005]; 
 2400:  0.11681571   0.004613  [0.7552 3.653  6.6936]
    vel: [ 0.0001 -0.0003  0.0003]; 
 3200:  0.11568572   0.002967  [0.7906 3.4423 6.9018]
    vel: [ 0.     -0.0002  0.0002]; 
 4000:  0.11521820   0.001909  [0.8133 3.3068 7.0357]
    vel: [ 0.     -0.0001  0.0001]; 
 4800:  0.11502477   0.001228  [0.8279 3.2196 7.1218]
    vel: [ 0.     -0.0001  0.0001]; 
 5600:  0.11494475   0.000790  [0.8373 3.1635 7.1772]
    vel: [ 0.     -0.0001  0.0001]; 
 6400:  0.11491164   0.000508  [0.8434 3.1274 7.2129]
    vel: [ 0. -0.  0.]; 
 7200:  0.11489794 

In [36]:
# Nesterov (pytorch)
update_func = functools.partial(update_wt_gd_nesterov_pytorch, momentum=0.0)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_nest00_pyt, loss_nest00_pyt = out
print('Predicted weights:', wt_nest00_pyt)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_wt_gd_nesterov_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.12614844   0.011150  [0.6148 4.49   5.8669]
    vel: [-0.0013  0.0079 -0.0078]; 
 1600:  0.11954696   0.007172  [0.7003 3.9806 6.37  ]
    vel: [-0.0008  0.0051 -0.005 ]; 
 2400:  0.11681571   0.004613  [0.7552 3.653  6.6936]
    vel: [-0.0005  0.0033 -0.0032]; 
 3200:  0.11568572   0.002967  [0.7906 3.4423 6.9018]
    vel: [-0.0004  0.0021 -0.0021]; 
 4000:  0.11521820   0.001909  [0.8133 3.3068 7.0357]
    vel: [-0.0002  0.0013 -0.0013]; 
 4800:  0.11502477   0.001228  [0.8279 3.2196 7.1218]
    vel: [-0.0001  0.0009 -0.0009]; 
 5600:  0.11494475   0.000790  [0.8373 3.1635 7.1772]
    vel: [-0.0001  0.0006 -0.0006]; 
 6400:  0.11491164   0.000508  [0.8434 3.1274 7.2129]
    vel: [-0.0001  0.0004 -0.0004]; 
 7200: 

As expected, the values match those from the basic gradient descent.

## momentum = 0.5
Now, we increase momentum to 0.5.  We compare against the corresponding runs of the plain momentum algorithm.

In [37]:
# Nesterov (classic)
update_func = functools.partial(update_wt_gd_nesterov_classic, momentum=0.5)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=12000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_nest50_cl, loss_nest50_cl = out
print('Predicted weights:', wt_nest50_cl)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_wt_gd_nesterov_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11955045   0.007175  [0.7002 3.981  6.3697]
    vel: [ 0.0002 -0.001   0.001 ]; 
 1600:  0.11568515   0.002966  [0.7906 3.4422 6.9019]
    vel: [ 0.0001 -0.0004  0.0004]; 
 2400:  0.11502448   0.001226  [0.8279 3.2194 7.122 ]
    vel: [ 0.     -0.0002  0.0002]; 
 3200:  0.11491155   0.000507  [0.8434 3.1273 7.213 ]
    vel: [ 0.     -0.0001  0.0001]; 
 4000:  0.11489225   0.000210  [0.8498 3.0892 7.2506]
    vel: [ 0. -0.  0.]; 
 4800:  0.11488895   0.000087  [0.8524 3.0735 7.2661]
    vel: [ 0. -0.  0.]; 
 5600:  0.11488839   0.000036  [0.8535 3.067  7.2726]
    vel: [ 0. -0.  0.]; 
 6400:  0.11488829   0.000015  [0.854  3.0643 7.2752]
    vel: [ 0. -0.  0.]; 
 7200:  0.11488828   0.000006  [0.8541 3.0632 7.2763]
 

In [38]:
# Nesterov (pytorch)
update_func = functools.partial(update_wt_gd_nesterov_pytorch, momentum=0.5)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=12000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_nest50_pyt, loss_nest50_pyt = out
print('Predicted weights:', wt_nest50_pyt)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_wt_gd_nesterov_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11954530   0.007175  [0.7003 3.9805 6.3702]
    vel: [-0.0017  0.0101 -0.01  ]; 
 1600:  0.11568427   0.002966  [0.7906 3.442  6.9022]
    vel: [-0.0007  0.0042 -0.0041]; 
 2400:  0.11502433   0.001226  [0.828  3.2193 7.1221]
    vel: [-0.0003  0.0017 -0.0017]; 
 3200:  0.11491153   0.000507  [0.8434 3.1273 7.213 ]
    vel: [-0.0001  0.0007 -0.0007]; 
 4000:  0.11489225   0.000210  [0.8498 3.0892 7.2506]
    vel: [-0.      0.0003 -0.0003]; 
 4800:  0.11488895   0.000087  [0.8524 3.0735 7.2661]
    vel: [-0.      0.0001 -0.0001]; 
 5600:  0.11488839   0.000036  [0.8535 3.067  7.2726]
    vel: [-0.      0.0001 -0.0001]; 
 6400:  0.11488829   0.000015  [0.854  3.0643 7.2752]
    vel: [-0.  0. -0.]; 
 7200:  0.11488828 

## momentum = 0.9

In [39]:
update_func = functools.partial(update_wt_gd_nesterov_classic, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=8000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_nest90_cl, loss_nest90_cl = out
print('Predicted weights:', wt_nest90_cl)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_wt_gd_nesterov_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11489109   0.000176  [0.8505 3.085  7.2548]
    vel: [ 0.     -0.0001  0.0001]; 
 1600:  0.11488827   0.000002  [0.8542 3.0626 7.2769]
    vel: [ 0. -0.  0.]; 
 2400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 3200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 4000:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 4800:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0. -0.  0.]; 
 5600:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0. -0.  0.]; 
 6400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0. -0.  0.]; 
 7200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0. -0.  0.]; 
 8000:  0.11

In [40]:
update_func = functools.partial(update_wt_gd_nesterov_pytorch, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=8000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
wt_nest90_pyt, loss_nest90_pyt = out
print('Predicted weights:', wt_nest90_pyt)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_wt_gd_nesterov_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11489106   0.000176  [0.8505 3.0849 7.2549]
    vel: [-0.0002  0.0013 -0.0013]; 
 1600:  0.11488827   0.000002  [0.8542 3.0626 7.2769]
    vel: [-0.  0. -0.]; 
 2400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 3200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 4000:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 4800:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [-0.  0. -0.]; 
 5600:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0.  0. -0.]; 
 6400:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0.  0. -0.]; 
 7200:  0.11488827   0.000000  [0.8543 3.0624 7.2771]
    vel: [ 0.  0. -0.]; 
 8000:  0.11

In [41]:
# Difference between ordinary momentum (pytorch) and Nesterov momentum (pytorch)
print('Momentum=0.0, max diff:', np.abs(loss_mom00_pyt - loss_nest00_pyt).max())
print('Momentum=0.5, max diff:', np.abs(loss_mom50_pyt - loss_nest50_pyt).max())
print('Momentum=0.9, max diff:', np.abs(loss_mom90_pyt - loss_nest90_pyt).max())

Momentum=0.0, max diff: 0.0
Momentum=0.5, max diff: 4.023921721423971
Momentum=0.9, max diff: 10.022383391012207


## Loss Trajectory -- Speed of Convergence
We find a similar behaviour in this algorithm as we found with momentum--the algorithm converges faster for larger values of the momentum coefficient.

In [42]:
labels = [f'momentum = {m:.2f}' for m in [0.0, 0.5, 0.9]]
w, h = 400, 300
s1 = display_losses(losses=[loss_nest00_cl, loss_nest50_cl, loss_nest90_cl],
                   labels=labels, width=w, height=h,
                   title='Losses -- Nesterov Classic Impl')
s2 = display_losses(losses=[loss_nest00_pyt, loss_nest50_pyt, loss_nest90_pyt],
                   labels=labels, width=w, height=h,
                   title='Losses -- Nesterov Pytorch Impl')
bkp.show(bokeh.layouts.row(s1, s2))

In [43]:
tol = 1e-9
nes00_c = np.argmax(np.isclose(loss_nest00_cl, loss_nest00_cl[-1], rtol=0, atol=tol))
nes50_c = np.argmax(np.isclose(loss_nest50_cl, loss_nest50_cl[-1], rtol=0, atol=tol))
nes90_c = np.argmax(np.isclose(loss_nest90_cl, loss_nest90_cl[-1], rtol=0, atol=tol))
print(f'classic impl: mom00={nes00_c}, mom50={nes50_c}, mom90={nes90_c}')
nes00_p = np.argmax(np.isclose(loss_nest00_pyt, loss_nest00_pyt[-1], rtol=0, atol=tol))
nes50_p = np.argmax(np.isclose(loss_nest50_pyt, loss_nest50_pyt[-1], rtol=0, atol=tol))
nes90_p = np.argmax(np.isclose(loss_nest90_pyt, loss_nest90_pyt[-1], rtol=0, atol=tol))
print(f'pytorch impl: mom00={nes00_p}, mom50={nes50_p}, mom90={nes90_p}')

classic impl: mom00=15511, mom50=7753, mom90=1484
pytorch impl: mom00=15511, mom50=7753, mom90=1483


## Comparison of Classic and Pytorch Implementations

In [44]:
labels = ['Basic Momentum', 'Nesterov']
w, h = 400, 300
s1 = display_losses([loss_mom50_cl, loss_nest50_cl], labels=labels,
                   width=w, height=h,
                   title='Loss -- Classic Impl -- momentum=0.50')
s2 = display_losses([loss_mom50_pyt, loss_nest50_pyt], labels=labels,
                   width=w, height=h,
                   title='Loss -- Pytorch Impl -- momentum=0.50')
s3 = display_losses([loss_mom90_cl, loss_nest90_cl], labels=labels,
                   width=w, height=h,
                   title='Loss -- Classic Impl -- momentum=0.90')
s4 = display_losses([loss_mom90_pyt, loss_nest90_pyt], labels=labels,
                   width=w, height=h,
                   title='Loss -- Pytorch Impl -- momentum=0.90')
bkp.show(bokeh.layouts.row([s1, s2]))
bkp.show(bokeh.layouts.row([s3, s4]))

**Observations**
 * Compared to the basic momentum algorithm, the Nesterov algorithm **oscillates less**.
 * The two implementations of Nesterov momentum--classic and pytorch--are similar.  For momentum=0.9, the classic implementation appears to oscillate less than the pytorch implementation.

## Exploding Gradient
The Nestorov Momentum Algorithm also suffers from the issue of gradients exploding if the learning rate is too large.  Show below is an example.  The learning rate chosen is close to the tipping point i.e. values slightly lower than this would result in proper convergence.

In [45]:
update_func = functools.partial(update_wt_gd_nesterov_pytorch, momentum=0.9)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20, learning_rate=0.6, loss_func=mse_loss, rseed=200127,
            print_iter=2)

Learning rate=0.6, Number of weights=3
Weight-update function=update_wt_gd_nesterov_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
    2: 202.93893870  22.714721  [-8.561  -1.4788 -0.1551]
    vel: [12.2465  4.2992  2.2256]; 
    4: 1199.57579190  52.125643  [-25.1931  -7.3406  -3.154 ]
    vel: [29.1227 13.0087  8.1393]; 
    6: 6967.22949340  125.220712  [-61.3638 -25.1317 -14.8787]
    vel: [67.6206 34.2654 23.0914]; 
    8: 40418.07951684  301.564503  [-146.364   -70.1035  -45.8024]
    vel: [161.0582  84.4349  57.9901]; 
   10: 234482.29964037  726.349807  [-350.9914 -178.4411 -120.5407]
    vel: [387.5545 203.7034 140.2496]; 
   12: 1360347.22639698  1749.506492  [-844.9785 -438.105  -299.3201]
    vel: [934.1501 489.8513 337.0918]; 
   14: 7892047.66114361  4213.912626  [-2036.0723 -1062.0948  -728.5277]
    vel: [2250.9705 1178.7772  810.8826]; 


# AdaGrad
AdaGrad, (Duchi et al., 2011), is an adaptive learning rate algorithm.  It adapts the learning rates of all parameters by scaling them in inverse proportion to the accumulated gradient values.  The values are accumulated as the square-root of the sum of the squares of the historical values.

The algorithm is defined as follows:

$$
\begin{align}
\boldsymbol{\mathbf{r}}_t &\leftarrow \boldsymbol{\mathbf{r}}_{t - 1} + 
    \boldsymbol{\hat{\mathbf{g}}}(\boldsymbol{\theta}_{t - 1}) \odot
    \boldsymbol{\hat{\mathbf{g}}}(\boldsymbol{\theta}_{t - 1}) \\
\boldsymbol{\epsilon}_t &\leftarrow 
    \frac{\epsilon_0}{\delta + \sqrt{\boldsymbol{\mathbf{r}}_t}} \\
\boldsymbol{\theta}_t &\leftarrow \boldsymbol{\theta}_{t - 1} - \boldsymbol{\epsilon}_t
    \odot \boldsymbol{\hat{\mathbf{g}}}(\boldsymbol{\theta}_{t - 1})
\end{align}
$$

where
$$
\begin{align}
\boldsymbol{\mathbf{\hat{g}}} &= \text{the gradient estimate at time $t$,} \\
\epsilon_{0} &= \text{the initial learning rate (scalar),} \\
\boldsymbol{\epsilon}_t &= \text{the learning rate at time $t$ (vector),} \\
\boldsymbol{\mathbf{r}}_t &= \text{a state variable that accumulates the gradients, at time $t$,} \\
\delta &= \text{a small constant for numerical stability,} \\
\boldsymbol{\theta}_t &= \text{the parameter vector at time $t$,} \\
\odot &= \text{the Hadamard product.}
\end{align}
$$


In [46]:
def update_adagrad(weights, x, y, lr, state=None, delta=1e-8,
                   fit_func=polynomial_function, grad_func=gradient_mse):
    Nweights = len(weights)
    if state is None:
        state = {'r': np.zeros(Nweights)}
    ypred = fit_func(weights, x)
    grad = grad_func(x, y, ypred, Nweights)
    state['r'] += grad * grad
    lr_t = lr / (delta + np.sqrt(state['r']))
    state['lr_t'] = lr_t
    weights[:] = weights - lr_t * grad
    return state, grad

We first run it with the same learning rate as before.

In [47]:
out = train(xtrain, ytrain, len(wt_true), update_adagrad,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800)
print(out[0])

Learning rate=0.1, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  1.49142879   0.830766  [2.243  3.1775 3.2613]
    r: [2833.8847 2189.7218 1604.9519]; lr_t: [0.0019 0.0021 0.0025]; 
 1600:  0.69614915   0.537411  [1.6616 3.7496 4.0993]
    r: [2957.5066 2283.4314 1755.6035]; lr_t: [0.0018 0.0021 0.0024]; 
 2400:  0.37016711   0.349400  [1.2795 4.1019 4.6262]
    r: [3012.8862 2319.765  1818.5796]; lr_t: [0.0018 0.0021 0.0023]; 
 3200:  0.23282156   0.228006  [1.0333 4.3248 4.9712]
    r: [3036.1501 2334.4768 1846.2257]; lr_t: [0.0018 0.0021 0.0023]; 
 4000:  0.17425989   0.149119  [0.8741 4.4647 5.2009]
    r: [3045.943  2340.2985 1858.6114]; lr_t: [0.0018 0.0021 0.0023]; 
 4800:  0.14908603   0.097784  [0.771  4.5506 5.3563]
    r: [3050.0538 2342.5039 1864.2964]; lr_t: [0.0018 0.0021 0.0023]; 


**Observations**
 * We see that the algorithm has not converged probably because of the dampening effect of the accumulated gradient term which would slow down the learning rate.
 * With $r > 1$, any term in the the learning rate vector at time $t$, $\boldsymbol{\epsilon}_t$, will always be smaller than the initial learning rate, $\epsilon_0$.  Moreover, $\boldsymbol{\epsilon}_t$ will always decrease with time.
 * The initial decrease in the learning rate is quite large (see the first printed value of `lr_t` above).
 * Because of the above observations, we could afford to increase the learning rate.  We will do so below.

## Increased Initial Learning Rate

Let's increase the learning rate from 0.1 to 1.0.  We have chosen this value so that the modified learning rate in Adagrad is close to 0.1.

Also, we will print out the first few values of the adapted learning rate.

In [48]:
# Print the learning rates for the first few iterations.
out = train(xtrain, ytrain, len(wt_true), update_adagrad,
            niter=8, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_iter=1)
print('-' * 80)
# Continue to convergence
out = train(xtrain, ytrain, len(wt_true), update_adagrad,
            niter=16000, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_iter=1000)
wt_ada1, loss_ada1 = out
print('Predicted weights:', out[0])
print('Basic gradient descent weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=1.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
    1: 12.09829764  10.977432  [1.4029 1.0183 0.7699]
    r: [69.3653 32.1852 18.9536]; lr_t: [0.1201 0.1763 0.2297]; 
    2:  7.03551978   6.706354  [1.9009 1.562  1.3285]
    r: [92.2387 45.6904 27.5501]; lr_t: [0.1041 0.1479 0.1905]; 
    3:  4.77162155   4.502685  [2.1933 1.924  1.7123]
    r: [100.865   52.5789  32.3095]; lr_t: [0.0996 0.1379 0.1759]; 
    4:  3.63632340   3.144699  [2.3678 2.1845 1.9991]
    r: [104.0309  56.4069  35.2047]; lr_t: [0.098  0.1331 0.1685]; 
    5:  3.01326077   2.275073  [2.4665 2.3809 2.2247]
    r: [105.0544  58.671   37.0931]; lr_t: [0.0976 0.1306 0.1642]; 
    6:  2.63633163   1.723024  [2.5145 2.5345 2.4093]
    r: [105.2972  60.0882  38.4019]; lr_t: [0.0975 0.129  0.1614]; 
    7:  2.38252604   1.3

**Observations**
 * The algorithm remains stable at a learning rate of 1.0.  The basic gradient descent (GD) algorithm becomes unstable at least at 0.8 for the given conditions.  This is unsurprising given the damping down of the learning rate by the algorithm occurs quite sharply in the first iteration itself (see the `lr_t` values in the first iteration above).
 * The algorithm converges around the 11,000th iteration.
 * The final parameter values are very close to the basic GD algo result.  This also allows us to skip plotting the fit result since it is essentially the same as the basic GD.
 * The learning rate for the three parameters decreases to around 0.1 by the first iteration itself.  By the eighth iteration itself the learning rate values have moved quite close to the final values.
 
### learning_rate = 10.0
Next, we increase the learning rate to 10.0 which is a rather large value.  Surprisingly the algorithm converges.

In [49]:
out = train(xtrain, ytrain, len(wt_true), update_adagrad,
            niter=2800, learning_rate=10.0, loss_func=mse_loss, rseed=200127,
            print_iter=400)
wt_ada10, loss_ada10 = out
print('Predicted weights:', out[0])
print('Basic gradient descent weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=10.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  400:  0.11529331   0.002171  [0.8079 3.334  7.0109]
    r: [852.5061 257.5362 128.9881]; lr_t: [0.3425 0.6231 0.8805]; 
  800:  0.11490536   0.000446  [0.8448 3.1182 7.2224]
    r: [852.5061 257.5366 128.9883]; lr_t: [0.3425 0.6231 0.8805]; 
 1200:  0.11488899   0.000092  [0.8523 3.0739 7.2659]
    r: [852.5062 257.5366 128.9883]; lr_t: [0.3425 0.6231 0.8805]; 
 1600:  0.11488830   0.000019  [0.8539 3.0648 7.2748]
    r: [852.5062 257.5366 128.9883]; lr_t: [0.3425 0.6231 0.8805]; 
 2000:  0.11488827   0.000004  [0.8542 3.0629 7.2766]
    r: [852.5062 257.5366 128.9883]; lr_t: [0.3425 0.6231 0.8805]; 
 2400:  0.11488827   0.000001  [0.8543 3.0625 7.277 ]
    r: [852.5062 257.5366 128.9883]; lr_t: [0.3425 0.6231 0.8805]; 
 2800:  0.1148882

**Observations**
 * The algorithm converges even for a large learning rate value of 10.0.
 * The algorithm converges in about 2,800 iterations.
 * Notice that the adapted learning rates are less than 1.0.

### learning rate of 1,000,000.0
Next, we try to increase the learning rate to a very high value of one million!  A rather absurd value, but done here in order to study the algorithm.

In [50]:
out = train(xtrain, ytrain, len(wt_true), update_adagrad,
            niter=3200, learning_rate=1000000.0, loss_func=mse_loss, rseed=200127,
            print_iter=400)
wt_ada, loss_ada = out
print('Predicted weights:', wt_ada)
print('Basic gradient descent weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=1000000.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  400:  0.11567904   0.003027  [0.7896 3.4419 6.9051]
    r: [1.2574e+13 3.9930e+12 2.0209e+12]; lr_t: [0.282  0.5004 0.7034]; 
  800:  0.11495075   0.000851  [0.8361 3.1691 7.1725]
    r: [1.2574e+13 3.9930e+12 2.0209e+12]; lr_t: [0.282  0.5004 0.7034]; 
 1200:  0.11489321   0.000239  [0.8492 3.0924 7.2477]
    r: [1.2574e+13 3.9930e+12 2.0209e+12]; lr_t: [0.282  0.5004 0.7034]; 
 1600:  0.11488866   0.000067  [0.8528 3.0708 7.2688]
    r: [1.2574e+13 3.9930e+12 2.0209e+12]; lr_t: [0.282  0.5004 0.7034]; 
 2000:  0.11488830   0.000019  [0.8539 3.0648 7.2748]
    r: [1.2574e+13 3.9930e+12 2.0209e+12]; lr_t: [0.282  0.5004 0.7034]; 
 2400:  0.11488827   0.000005  [0.8542 3.0631 7.2764]
    r: [1.2574e+13 3.9930e+12 2.0209e+12]; lr_t: [

**Observations**
 * Surprisingly, the algorithm converges!
 * Notice the rather high values of the state variable, `r`, which accumulates the gradient values.  This acts as a damping factor to the initial learning rate and immediately reduces the actual learning rate used to a small value.

# Adam
Adam, (Kingma and Ba, 2014), is another adaptive learning rate stochastic gradient descent algorithm.  In a way, it is a combination of the RMSProp and Momentum.

The updates are as follows:
$$
\begin{align*}
\mathbf{m}_t & \leftarrow \beta_1 \, \mathbf{m}_{t - 1} +
    (1 - \beta_1) \, \mathbf{g}(\boldsymbol{\theta}_{t - 1}) \\
\mathbf{v}_t & \leftarrow \beta_2 \, \mathbf{v}_{t - 1}
        + (1 - \beta_2) \, \mathbf{g}(\boldsymbol{\theta}_{t - 1}) \odot
        \mathbf{g}(\boldsymbol{\theta}_{t - 1}) \\
\hat{\mathbf{m}}_t & \leftarrow \frac{\mathbf{m}_t}{1 - \beta_1^t} \\
\hat{\mathbf{v}}_t & \leftarrow \frac{\mathbf{v}_t}{1 - \beta_2^t} \\
\boldsymbol{\theta}_t & \leftarrow \boldsymbol{\theta}_{t - 1} - 
    \epsilon \frac{\hat{\mathbf{m}}_t}{\delta + \sqrt{\hat{\mathbf{v}}}_t}
\end{align*}
$$
where
$$
\begin{align*}
\mathbf{g} &= \text{the gradient estimate} \\
\beta_1, \beta_2 &= \text{exponential decay rate constants} \\
\mathbf{m}_t, \hat{\mathbf{m}}_t &=
    \text{biased and unbiased first moment estimate at time $t$} \\
\mathbf{v}_t, \hat{\mathbf{v}}_t &=
    \text{biased and unbiased second moment estimate at time $t$} \\
\boldsymbol{\theta}_t &= \text{model parameters at time $t$} \\
\epsilon &= \text{the initial learning rate} \\
\delta &= a \text{small constant for numerical stability} \\
\end{align*}
$$

In [51]:
def update_adam(weights, x, y, lr, state=None,
                betas=(0.9, 0.99), delta=1e-8,
                do_bias_correction=True, fit_func=polynomial_function,
                grad_func=gradient_mse):
    Nweights = len(weights)
    if state is None:
        state = {
            'm': np.zeros(Nweights),
            'v': np.zeros(Nweights),
            'b1^t': 1.0,
            'b2^t': 1.0,
        }
    ypred = fit_func(weights, x)
    grad = grad_func(x, y, ypred, Nweights)
    m, v = state['m'], state['v']
    b1, b2 = betas
    state['m'] = m = b1 * m + (1 - b1) * grad
    state['v'] = v = b2 * v + (1 - b2) * (grad * grad)
    if do_bias_correction:
        state['b1^t'] *= b1
        state['b2^t'] *= b2
        mhat = m / (1.0 - state['b1^t'])
        vhat = v / (1.0 - state['b2^t'])
    else:
        mhat, vhat = m, v
    weights[:] = weights - lr * mhat / (delta + np.sqrt(vhat))
    return state, grad

A training run of the Adam algorithm is below.  The number of iterations was increased to more than triple since the algorithm didn't quite converge like the others.  The printing of the state information has been suppressed to focus on the loss and the gradient.

In [52]:
update_func = functools.partial(update_adam)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800, print_state=False)
wt_adam, loss_adam = out
print('Predicted weights:', wt_adam)
print('Basic gradient descent weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11489818   0.000340  [0.8471 3.1048 7.2354]
 1600:  0.11488889   0.000929  [0.8547 3.0628 7.2775]
 2400:  0.11489166   0.004791  [0.8533 3.0614 7.2761]
 3200:  0.11491226   0.014922  [0.8569 3.065  7.2797]
 4000:  0.11489168   0.004148  [0.8533 3.0614 7.2761]
 4800:  0.11494116   0.013705  [0.8504 3.0585 7.2732]
 5600:  0.11493766   0.000364  [0.858  3.0662 7.2809]
 6400:  0.11490268   0.007703  [0.8563 3.0644 7.2791]
 7200:  0.11488859   0.001826  [0.854  3.0621 7.2768]
 8000:  0.11493550   0.013979  [0.858  3.0661 7.2808]
 8800:  0.11489250   0.003542  [0.8554 3.0635 7.2782]
 9600:  0.11488829   0.002722  [0.8544 3.0625 7.2772]
10400:  0.11489218   0.006132  [0.8553 3.0635 7.2782]
11200:  0.11497058   0.021493  [0.8591 3.0673 7.282

In [53]:
s1 = display_losses([loss_gdb, loss_adam], width=400, height=300,
                    labels=['GD', 'Adam'], title='Loss Trajectory -- Adam and Basic GD')
s2 = display_losses([loss_gdb, loss_adam], width=400, height=300,
                    labels=['GD', 'Adam'], title='Loss Trajectory -- Adam and Basic GD')
tmp1, tmp2 = min(len(loss_gdb), len(loss_adam)) - 400, max(len(loss_gdb), len(loss_adam)) + 10
s2.x_range.start = tmp1
s2.x_range.end = tmp2
s2.y_range.start = min(loss_gdb[tmp1:tmp2]) * 0.999
s2.y_range.end = max(loss_gdb[tmp1:tmp2]) * 1.005
bkp.show(bokeh.layouts.row(s1, s2))

**Observations**
 * For the given conditions, the Adam optimizer takes about the same number of iterations as the basic gradient descent algorithm.
 * From the figure to the left above, the decrease in loss is more gradual in Adam as compared to the basic GD. 
 * Overall, the loss trajectory looks smooth.  But, on closer examimation, it does not converge as smoothly as the basic GD or the other algorithms--there are micro oscillations even after 32,000 iterations (twice the point where it has basically converged).  This can be seen in the figure to the right above.

## $\beta_1$ and $\beta_2$ Trajectories
Below is a training run that also prints the state information.  We limit the number of iterations.

In [54]:
update_func = functools.partial(update_adam)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=9600, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800, print_state=True)
print('Predicted weights:', out[0])
print('Basic gradient descent weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11489818   0.000340  [0.8471 3.1048 7.2354]
    m: [-0.0001  0.0003 -0.0003]; v: [0.0024 0.0012 0.0008]; b1^t: 2.4774651351228073e-37; b2^t: 0.00032222236288023367; 
 1600:  0.11488889   0.000929  [0.8547 3.0628 7.2775]
    m: [-0.0001 -0.     -0.    ]; v: [0.0001 0.     0.    ]; b1^t: 6.137833495749071e-74; b2^t: 1.0382725114012107e-07; 
 2400:  0.11489166   0.004791  [0.8533 3.0614 7.2761]
    m: [0.0002 0.0001 0.0001]; v: [0.0001 0.     0.    ]; b1^t: 1.5206268490907254e-110; b2^t: 3.345546219372925e-11; 
 3200:  0.11491226   0.014922  [0.8569 3.065  7.2797]
    m: [-0.0006 -0.0003 -0.0002]; v: [0.0001 0.     0.    ]; b1^t: 3.767300002153909e-147; b2^t: 1.0780098079313767e-14; 
 4000:  0.11489168   0.004148  [0.8533 3.0614 7.2761]

**Observations**
 * The values of $\beta_1$ are quite insignificant in the 800th iteration itself.  $\beta_2$ decreases more slowly since we have chosen a higher value for $\beta_2$ (0.99) than for $\beta_1$ (0.9).  $\beta_2$ too becomes insignificant--less than 1e-10--after 2,400 iterations.

## Turning Off Bias Correction
In the training run below we turn off the bias correction.  Let's see what happens.

In [55]:
update_func = functools.partial(update_adam, do_bias_correction=False)
out = train(xtrain, ytrain, len(wt_true), update_func,
            niter=20000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=800, print_state=False)
print('Predicted weights:', out[0])
print('Basic gradient descent weights:', wt_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 26.97074690  10.977432  [ 0.4029  0.0183 -0.2301]
  800:  0.11488894   0.000089  [0.8524 3.0734 7.2663]
 1600:  0.11489719   0.009115  [0.8527 3.0608 7.2755]
 2400:  0.11489668   0.001701  [0.8527 3.0609 7.2755]
 3200:  0.11489283   0.006091  [0.8531 3.0613 7.276 ]
 4000:  0.11489078   0.002736  [0.8551 3.0633 7.2779]
 4800:  0.11489701   0.008177  [0.8527 3.0608 7.2755]
 5600:  0.11488925   0.001619  [0.8537 3.0619 7.2766]
 6400:  0.11489841   0.008133  [0.856  3.0641 7.2788]
 7200:  0.11489054   0.001966  [0.8551 3.0632 7.2779]
 8000:  0.11492199   0.010674  [0.8574 3.0655 7.2802]
 8800:  0.11489598   0.007113  [0.8528 3.0609 7.2756]
 9600:  0.11488841   0.003310  [0.8545 3.0626 7.2773]
10400:  0.11488862   0.015977  [0.854  3.0621 7.2768]
11200:  0.11489112   0.007265  [0.8552 3.0633 7.278

In [56]:
p = display_losses([loss_adam, out[1]], labels=['Bias correction', 'No correction'])
bkp.show(p)

**Observations**
 * For the given conditions, the difference is indiscernible.

# Part II -- 1e-10 factor
 3. Replace $\alpha + \beta x + \gamma x^2$ with $\alpha + \beta x + 10^{-10} \, \gamma x^2$ and simultaneously make the value of $\gamma_\text{true}$ $10^{10}$ times larger than previously. Then check again the performance of 
    1. Gradient descent (already finished)
    1. Gradient descent with momentum
    1. Gradient descent with Nesterov momentum
    1. AdaGrad
    1. Adam

And check the mean-square error after the optimizer completes its iterations.

**Solution**
The function `polynomial_function` takes an additional optional parameter where additional factors can be specified.  Accordingly, the function `gradient_mse` also takes an optional parameter in order to specify the same factors.

Additionally, the update function for each of the algorithms also takes optional parameters to specify the fitting (polynomial) function and the gradient function.

We use the tools above along with `functools.partial` to meet our needs.

## Training Data
We specify the true weight and generate the training data below.

In [57]:
wt1_true = np.array([1.0, 2.0, 8.0 * 1e+10])
factors = np.array([1, 1, 1e-10])
fit_func = functools.partial(polynomial_function, factors=factors)
grad_func = functools.partial(gradient_mse, factors=factors)
xtrain1, ytrain1 = gen_training_data(wt1_true, seed=200127, fit_func=fit_func)
p = display_poly_fit(xtrain1, ytrain1, wt1_true, fit_func=fit_func,
                    title='Training Data')
bkp.show(p)

## Basic Gradient Descent
Below is a training run for the basic gradient descent algorithm.

In [58]:
# init_weights=[0.4029198531683306, 0.0183499610911668, -0.2300722413704090]
update_func = functools.partial(update_gradient_descent_basic,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=1000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_iter=100)
wt1_gdb, loss1_gdb = out
print('Predicted weights:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_basic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
  100:  0.78377067   0.326393  [ 0.7883  8.0928 -0.2301]
  200:  0.43223802   0.081111  [ 0.0021  9.6557 -0.2301]
  300:  0.41052896   0.020157  [-0.1933 10.0441 -0.2301]
  400:  0.40918831   0.005009  [-0.2418 10.1406 -0.2301]
  500:  0.40910552   0.001245  [-0.2539 10.1646 -0.2301]
  600:  0.40910040   0.000309  [-0.2569 10.1706 -0.2301]
  700:  0.40910009   0.000077  [-0.2576 10.172  -0.2301]
  800:  0.40910007   0.000019  [-0.2578 10.1724 -0.2301]
  900:  0.40910007   0.000005  [-0.2579 10.1725 -0.2301]
 1000:  0.40910007   0.000001  [-0.2579 10.1725 -0.2301]
Loss values: Last: 0.409100, Average (last 10): 0.409100
Total time: 0.15 sec
Predicted weights: [-0.2579 10.1725 -0.2301]
True weights: [1.0, 2.0, 8.0]


In [59]:
p = display_poly_fit(xtrain1, ytrain1, wt1_true, wt_preds=[wt1_gdb],
                     fit_func=fit_func)
bkp.show(p)

**Observations**
 * The algorithm converges very quickly to the final solution.  By the 600th iteration itself it has converged.
 * The solution is basically a straight line!!  This is because the weight $w_2$ is around -0.23 and when combined with the $10^{-10}$ factor is insignificant compared to the weight $w_1$ whose value is around $10$.
 * The predicted weight $w_2$ is pretty much the same as its initial value before the start of gradient descent.  This is because the gradient for $w_2$ is tiny because of the $10^{-10}$ factor.

Let's look at this more closely.

The prediction model is
$$
\hat{y} = w_0 + w_1 x + 10^{-10} \, w_2 x^2
$$

The gradient component for $w_2$, $g_2$, for a single sample is
$$
g_2 = \frac{\partial L}{\partial w_2} = 2 (\hat{y} - y) 10^{-10} \, x^2
$$

Hence $g_2$ is very small because of the $10^{-10}$ factor.

Now, the gradient descent update for $w_2$ is
$$
w_2 \leftarrow w_2 - \epsilon g_2
$$
where $\epsilon$ is the learning rate.

Hence the updated $w_2$ is practically the same as its old value.  And the algorithm basically returns the initialized value of $w_2$.

### $R^2$ value

In [60]:
Rsquared(ytrain1, loss1_gdb[-1])

0.95576401221208

## Gradient Descent with Momentum

In [61]:
update_func = functools.partial(update_gradient_descent_momentum_classic,
                                momentum=0.9,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=1000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=100)
wt1_mom90, loss1_mom90 = out
print('Predicted weights:', wt1_mom90)
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_gradient_descent_momentum_classic
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
  100:  0.40921121   0.041402  [-0.2761 10.1927 -0.2301]
  200:  0.40910008   0.000061  [-0.2579 10.1728 -0.2301]
  300:  0.40910007   0.000001  [-0.2579 10.1725 -0.2301]
  400:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  500:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  600:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  700:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  800:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  900:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
 1000:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
Loss values: Last: 0.409100, Average (last 10): 0.409100
Total time: 0.11 sec
Predicted weights: [-0.2579 10.1725 -0.2301]
Basic GD result: [-0.2579 10.17

**Observations**
 * We get the same result as we did with basic gradient descent.
 * The expression for the gradient is the same--it does not depend on the algorithm.  And since its value is small, $w_2$ practically does not get updated.

## Nesterov Momentum

In [62]:
update_func = functools.partial(update_wt_gd_nesterov_pytorch,
                                momentum=0.9,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=1000, learning_rate=0.2, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=100)
wt1_nes90, loss1_nes90 = out
print('Predicted weights:', wt1_nes90)
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=0.2, Number of weights=3
Weight-update function=update_wt_gd_nesterov_pytorch
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
  100:  0.40911008   0.001755  [-0.2633 10.1833 -0.2301]
  200:  0.40910007   0.000002  [-0.2579 10.1725 -0.2301]
  300:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  400:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  500:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  600:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  700:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  800:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
  900:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
 1000:  0.40910007   0.000000  [-0.2579 10.1725 -0.2301]
Loss values: Last: 0.409100, Average (last 10): 0.409100
Total time: 0.11 sec
Predicted weights: [-0.2579 10.1725 -0.2301]
Basic GD result: [-0.2579 10.1725 -0.2301]

**Observations**
 * Our results for Nesterov momentum are essentially the same as that for momentum.

## AdaGrad

In [63]:
update_func = functools.partial(update_adagrad,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=20000, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=2000)
wt1_adag, loss1_adag = out
print('Predicted weights:', wt1_adag)
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=1.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 2000:  0.40910007   0.000000  [-0.2579 10.1725  2.0828]
 4000:  0.40910007   0.000000  [-0.2579 10.1725  3.5406]
 6000:  0.40910007   0.000000  [-0.2579 10.1725  4.9908]
 8000:  0.40910007   0.000000  [-0.2579 10.1725  6.4338]
10000:  0.40910007   0.000000  [-0.2579 10.1725  7.87  ]
12000:  0.40910007   0.000000  [-0.2579 10.1725  9.2998]
14000:  0.40910007   0.000000  [-0.2579 10.1725 10.7234]
16000:  0.40910007   0.000000  [-0.2579 10.1725 12.1411]
18000:  0.40910007   0.000000  [-0.2579 10.1725 13.5531]
20000:  0.40910007   0.000000  [-0.2579 10.1725 14.9597]
Loss values: Last: 0.409100, Average (last 10): 0.409100
Total time: 2.08 sec
Predicted weights: [-0.2579 10.1725 14.9597]
Basic GD result: [-0.2579 10.1725 -0.2301]
True weights: 

**Observations**
 * After 20,000 iterations, the loss has converged, and so have $w_0$ and $w_1$.  But $w_2$ has not.
 * The gradient is vanishing!
 * The reason for this is the $\delta$ term in the denominator that was added for numerical stability.  Because the value of $r_2$ in the denominator is small, it is now comparable to the default $\delta$ value of $10^{-8}$.
 * Also, the converged values of $w_0$ and $w_1$ are the same as for the basic GD.
 * As a follow up--what is practical situation when $\delta$ is useful?  Would it be better to drop it and have the algorithm fail so it catches the attention of the operator?

Below we print the values of the denominator term for inspection.  We see that $r_2$ is indeed small.

In [64]:
np.set_printoptions(precision=None, suppress=False)
update_func = functools.partial(update_adagrad,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=20000, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_state=True, print_iter=2000)
np.set_printoptions(precision=4, suppress=True)

Learning rate=1.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 2000:  0.40910007   0.000000  [-0.2579 10.1725  2.0828]
    r: [1.2779e+02 1.1029e+02 1.1304e-18]; lr_t: [8.8459e-02 9.5219e-02 9.0390e+07]; 
 4000:  0.40910007   0.000000  [-0.2579 10.1725  3.5406]
    r: [1.2779e+02 1.1029e+02 1.2611e-18]; lr_t: [8.8459e-02 9.5219e-02 8.9904e+07]; 
 6000:  0.40910007   0.000000  [-0.2579 10.1725  4.9908]
    r: [1.2779e+02 1.1029e+02 1.3919e-18]; lr_t: [8.8459e-02 9.5219e-02 8.9447e+07]; 
 8000:  0.40910007   0.000000  [-0.2579 10.1725  6.4338]
    r: [1.2779e+02 1.1029e+02 1.5227e-18]; lr_t: [8.8459e-02 9.5219e-02 8.9016e+07]; 
10000:  0.40910007   0.000000  [-0.2579 10.1725  7.87  ]
    r: [1.2779e+02 1.1029e+02 1.6534e-18]; lr_t: [8.8459e-02 9.5219e-02 8.8606e+07]; 
12000:  0.40910007   0.000000  [-0.

### Using a smaller $\delta$
Let us try with a smaller value of $\delta$, say, $10^{-20}$.

In [65]:
np.set_printoptions(precision=None, suppress=False)
update_func = functools.partial(update_adagrad, delta=1e-20,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=20000, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_state=True, print_iter=2000)
wt1_adag1, loss1_adag1 = out
print('Predicted weights:', wt1_adag1)
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)
np.set_printoptions(precision=4, suppress=True)

Learning rate=1.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 2000:  0.40910007   0.000000  [-0.2579 10.1725 27.0046]
    r: [1.2779e+02 1.1029e+02 1.1304e-18]; lr_t: [8.8459e-02 9.5219e-02 9.4057e+08]; 
 4000:  0.40910007   0.000000  [-0.2579 10.1725 41.799 ]
    r: [1.2779e+02 1.1029e+02 1.2611e-18]; lr_t: [8.8459e-02 9.5219e-02 8.9047e+08]; 
 6000:  0.40910007   0.000000  [-0.2579 10.1725 55.8444]
    r: [1.2779e+02 1.1029e+02 1.3919e-18]; lr_t: [8.8459e-02 9.5219e-02 8.4761e+08]; 
 8000:  0.40910007   0.000000  [-0.2579 10.1725 69.244 ]
    r: [1.2779e+02 1.1029e+02 1.5227e-18]; lr_t: [8.8459e-02 9.5219e-02 8.1040e+08]; 
10000:  0.40910007   0.000000  [-0.2579 10.1725 82.0797]
    r: [1.2779e+02 1.1029e+02 1.6534e-18]; lr_t: [8.8459e-02 9.5219e-02 7.7769e+08]; 
12000:  0.40910007   0.000000  [-0.

**Observations**
 * The loss value appears to have converged, and so have $w_0$ and $w_1$ to the same values as in basic GD.  But $w_2$ has not and continues to grow.  Because of the $10^{-10}$ factor and given that the $w_2$ values are not that large, we surmise that the growth in $w_2$ does not affect the loss value.
 * If the learning rate is increased, then $w_2$ grows to larger values.  And neither the loss trajectory nor the converged values of $w_0$ and $w_1$ are changed.

### What about $\delta=0$?
Let's try setting $\delta$ to zero.  Also, we increase the learning rate.

In [66]:
np.set_printoptions(precision=None, suppress=False)
update_func = functools.partial(update_adagrad, delta=0,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=20000, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_state=True, print_iter=2000, sample_iter=1000)
print('Predicted weights:', out[0])
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)
np.set_printoptions(precision=4, suppress=True)

Learning rate=1.0, Number of weights=3
Weight-update function=update_adagrad
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 2000:  0.40910007   0.000000  [-0.2579 10.1725 27.0046]
    r: [1.2779e+02 1.1029e+02 1.1304e-18]; lr_t: [8.8459e-02 9.5219e-02 9.4057e+08]; 
 4000:  0.40910007   0.000000  [-0.2579 10.1725 41.799 ]
    r: [1.2779e+02 1.1029e+02 1.2611e-18]; lr_t: [8.8459e-02 9.5219e-02 8.9047e+08]; 
 6000:  0.40910007   0.000000  [-0.2579 10.1725 55.8444]
    r: [1.2779e+02 1.1029e+02 1.3919e-18]; lr_t: [8.8459e-02 9.5219e-02 8.4761e+08]; 
 8000:  0.40910007   0.000000  [-0.2579 10.1725 69.244 ]
    r: [1.2779e+02 1.1029e+02 1.5227e-18]; lr_t: [8.8459e-02 9.5219e-02 8.1040e+08]; 
10000:  0.40910007   0.000000  [-0.2579 10.1725 82.0797]
    r: [1.2779e+02 1.1029e+02 1.6534e-18]; lr_t: [8.8459e-02 9.5219e-02 7.7769e+08]; 
12000:  0.40910007   0.000000  [-0.

In [67]:
np.set_printoptions(precision=None, suppress=False)
update_func = functools.partial(update_adagrad, delta=0,
                                grad_func=grad_func, fit_func=fit_func)
# out = train(xtrain1, ytrain1, len(wt1_true), update_func,
#             fit_func=fit_func, grad_func=grad_func,
#             niter=1000000, learning_rate=100.0, loss_func=mse_loss, rseed=200127,
#             print_state=True, print_iter=100000, sample_iter=1000000)
# print('Predicted weights:', out[0][0], out[0][1], out[0][2])
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)
np.set_printoptions(precision=4, suppress=True)

Basic GD result: [-0.2579 10.1725 -0.2301]
True weights: [1.0, 2.0, 8.0]


In [68]:
print('Predicted weights:', out[0][0], out[0][1], out[0][2])

Predicted weights: -0.25788939254871784 10.17252795910107 139.73673127159515


**Observations**
 * Beyond a certain learning rate (e.g. 100), the trajectory of $w_2$ appears to follow the same path.  See the table below which shows the values of the learning rates, the values of $r_2$ (the component of $r$ corresponding to $w_2$), the value of $w_2$, and the loss value, $L$.  The consistency of $w_2$ at the end of 32k iterations is surprising.  A partial explanation is that the value of $r_2$ also increases and saturates the adapted learning rate at 9.4189e+09.  It is unclear why the value of $r_2$ adjusts this way.  Of course, the values of learning rates used here are absurd for practical applications.

| Learning Rate |      $r_2$ | $w_2$ at 32k | $L$ at 32k |
|--------------:|-----------:|-------------:|------------:
|           100 |   1.05e-16 |      2,535.9 | 0.40910005 |
|         1,000 | 1.1184e-14 |      2,461.2 | 0.40910005 |
|        10,000 | 1.1263e-12 |      2,452.5 | 0.40910005 |
|     1,000,000 | 1.1272e-08 |      2,451.5 | 0.40910005 |

## Adam

Below, we run the Adam optimizer setting the learing rate to 4.0.

First we show the run without printing the state values.  Next, we re-run with printing of the state values.

In [69]:
np.set_printoptions(precision=None, suppress=False)
update_func = functools.partial(update_adam,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=24000, learning_rate=4.0, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=2000)
print()
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=24000, learning_rate=4.0, loss_func=mse_loss, rseed=200127,
            print_state=True, print_iter=2000)
print('Predicted weights:', out[0])
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)
np.set_printoptions(precision=4, suppress=True)

Learning rate=4.0, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 2000:  0.41655999   0.199600  [-0.2002 10.2302  6.6322]
 4000:  0.40954185   0.377229  [-0.2438 10.1866 13.0914]
 6000:  0.72199367   1.280508  [-0.6315  9.7989 19.5505]
 8000:  0.43066659   0.191162  [-0.356  10.0744 26.0103]
10000:  0.40921689   0.039445  [-0.2507 10.1797 32.4699]
12000:  0.41441256   0.135118  [-0.3066 10.1238 38.9293]
14000:  0.40928832   0.365846  [-0.2671 10.1634 45.3888]
16000:  0.71290829   0.874801  [-0.6261  9.8044 51.8477]
18000:  0.40952100   0.061277  [-0.2442 10.1862 58.3074]
20000:  0.40999558   0.056982  [-0.2779 10.1525 64.7668]
22000:  0.41483209   0.285118  [-0.3085 10.122  71.2262]
24000:  0.40911590   0.021222  [-0.2605 10.1699 77.6858]
Loss values: Last: 0.409116, Average (last 10): 0.414941
Total time: 

**Observations**
 * The loss hasn't quite converged after 32,000 iterations even though we have significantly increased the learning rate.  Neither have the weight values.
 * As with AdaGrad, we note that $\delta$ is significant with respect to the other denominator term $\sqrt{v_t}$.  For example, in the 24,000th iteration, with $\epsilon=4.0$, we see $v_2 = 1.88 x 10^{-22}$ or $\sqrt{v_2} = 1.37 x 10^{-11}$ which is smaller than $\delta = 10^{-8}$.

### Decrease $\delta$
As with AdaGrad, we will decrease the value of $\delta$ and re-run.

**Learning Rate=0.10**
First, we run with a learning rate of 0.1.  We also run with 1.0 and 10.0.

In [70]:
update_func = functools.partial(update_adam, delta=1e-30,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=48000, learning_rate=0.1, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=4000)
wt1_adam_01, loss1_adam_01 = out
print('Predicted weights:', out[0])
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=0.1, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 4000:  0.40910068   0.002998  [ -0.2574  10.1731 357.3841]
 8000:  0.40919205   0.023477  [ -0.2643  10.1661 757.1024]
12000:  0.40910150   0.004877  [  -0.2571   10.1733 1156.8266]
16000:  0.40910162   0.002392  [  -0.2587   10.1717 1556.5565]
20000:  0.40910023   0.001279  [  -0.2582   10.1722 1956.2841]
24000:  0.40910429   0.000224  [  -0.2593   10.1712 2356.0104]
28000:  0.40911307   0.010735  [  -0.2555   10.1749 2755.7421]
32000:  0.40910099   0.011035  [  -0.2572   10.1732 3155.4675]
36000:  0.40917364   0.019021  [  -0.2636   10.1668 3555.2005]
40000:  0.40910110   0.004519  [  -0.2572   10.1732 3954.927 ]
44000:  0.40910068   0.007910  [  -0.2584   10.172  4354.6545]
48000:  0.40911408   0.003386  [  -0.2554   10.175  4754.3639]
Los

**Observations**
 * The loss value seems to be converging around 0.4091, although we see a slight increase towards the end.  As we have seen before, the Adam optimizer does not converge smoothly.
 * The value of $w_2$ continues to increase and does not converge.
 * $w_0$ and $w_1$ converge to values close to that seen with basic GD.
 * The predicted $w_2$ is not large enough to offset the $10^{-10}$ factor, and hence the fit is practically linear.

**Learning Rate=1.0**

In [71]:
update_func = functools.partial(update_adam, delta=1e-30,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=48000, learning_rate=1.0, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=4000)
wt1_adam_10, loss1_adam_10 = out
print('Predicted weights:', out[0])
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=1.0, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 4000:  0.40911191   0.007390  [  -0.2556   10.1748 3461.1373]
 8000:  0.41227095   0.096314  [  -0.2955   10.1349 7213.5256]
12000:  0.41737375   0.216627  [   -0.1971    10.2333 10967.8725]
16000:  0.40915465   0.015612  [   -0.2628    10.1676 14713.7109]
20000:  0.41061219   0.071267  [   -0.2319    10.1985 18462.827 ]
24000:  0.41247844   0.101162  [   -0.2191    10.2114 22210.9303]
28000:  0.40914765   0.063789  [   -0.2625    10.1679 25959.6976]
32000:  0.41087518   0.093623  [   -0.2297    10.2007 29710.8562]
36000:  0.40921404   0.024723  [   -0.2507    10.1797 33460.3315]
40000:  0.40926080   0.010327  [   -0.2494    10.181  37213.3058]
44000:  0.40991627   0.092400  [   -0.2388    10.1916 40965.3255]
48000:  0.41106895   0.129619  [ 

**Observations**
 * The algorithm is showing more signs of variability in the loss values even at the end of the run.
 * $w_2$ increases as before, but the values are higher than that obtained with a learning rate of 0.1.
 * There is a slight decrease in the final value of $w_1$, perhaps because of the larger value of $w_2$.
 * The predicted $w_2$ is not large enough to offset the $10^{-10}$ factor, and hence the fit is practically linear.

**Learning Rate=3.0**

In [72]:
update_func = functools.partial(update_adam, delta=1e-30,
                                grad_func=grad_func, fit_func=fit_func)
out = train(xtrain1, ytrain1, len(wt1_true), update_func,
            fit_func=fit_func, grad_func=grad_func,
            niter=48000, learning_rate=3.0, loss_func=mse_loss, rseed=200127,
            print_state=False, print_iter=4000)
wt1_adam_30, loss1_adam_30 = out
print('Predicted weights:', out[0])
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)

Learning rate=3.0, Number of weights=3
Weight-update function=update_adam
Initial weights: 0.4029198531683306, 0.0183499610911668, -0.2300722413704090
 Iter         Loss   Gradient  Weights
    0: 25.97863622   9.902766  [ 0.4029  0.0183 -0.2301]
 4000:  0.41705405   0.043321  [  -0.3175   10.113  7492.225 ]
 8000:  0.41143605   0.039446  [   -0.2256    10.2048 15566.2896]
12000:  0.43144233   0.409576  [   -0.158     10.2724 23547.7131]
16000:  0.42335406   0.236646  [   -0.1781    10.2523 31580.076 ]
20000:  0.43440159   0.610941  [   -0.1516    10.2788 39648.0585]
24000:  0.41038743   0.075880  [   -0.2339    10.1965 47654.5666]
28000:  0.41097963   0.085280  [   -0.2289    10.2015 55644.485 ]
32000:  0.41063827   0.060249  [   -0.2317    10.1987 63655.7078]
36000:  0.41445379   0.009861  [   -0.209     10.2214 71673.5673]
40000:  0.41130901   0.446890  [   -0.2893    10.1411 79629.7398]
44000:  0.40982594   0.082557  [   -0.2399    10.1905 87620.0561]
48000:  0.45015672   0.400008 

**Observations**
 * The algorithm is showing more signs of variability in the loss values--even more than what we saw for a learning rate of 1.0.
 * $w_2$ increases as before, but the values are higher than that obtained with a learning rate of 1.0.
 * The decrease in the final value of $w_1$ is more pronounced, perhaps because of the even larger value of $w_2$.
 * The predicted $w_2$ is not large enough to offset the $10^{-10}$ factor, and hence the fit is practically linear.

In [73]:
# Trials
np.set_printoptions(precision=None, suppress=False)
# update_func = functools.partial(update_adam, delta=0,
#                                 grad_func=grad_func, fit_func=fit_func)
# out = train(xtrain1, ytrain1, len(wt1_true), update_func,
#             fit_func=fit_func, grad_func=grad_func,
#             niter=1000000, learning_rate=3.0, loss_func=mse_loss, rseed=200127,
#             print_state=True, print_iter=200000, sample_iter=200000)
# print('Predicted weights:', out[0], f'[{out[0][0]:.04f} {out[0][1]:.04f} {out[0][2]:.5g}]')
print('Basic GD result:', wt1_gdb)
print('True weights:', wt_true)
np.set_printoptions(precision=4, suppress=True)

Basic GD result: [-0.2579 10.1725 -0.2301]
True weights: [1.0, 2.0, 8.0]


In [74]:
np.sqrt(1.3838e-22)

1.1763502879669814e-11

In [75]:
labels=['lr=0.1', 'lr=1.0', 'lr=3.0']
w, h = 400, 300
s1 = display_losses([loss1_adam_01, loss1_adam_10, loss1_adam_30], labels=labels,
                   width=w, height=h)
s2 = display_poly_fit(xtrain, ytrain, wt1_true, [wt1_adam_01, wt1_adam_10, wt1_adam_30],
                      fit_func=fit_func,
                      labels=labels, width=w, height=h)
bkp.show(bokeh.layouts.row(s1, s2))

**Overall Observations for the Adam Optimizer**
 * The fits are practically linear since the predicted value of $w_2$ is not large enough to offset the $10^{-10}$ factor, even though larger values of $w_2$ are obtained for larger values of the learning rate.
 * Accounting for the small value of $\delta$ does not help with getting a quadratic fit.
 * Variability of the loss trajectory increases as the learning rate increases.  This may be best seen in the left figure above.

# References
 1. Duchi, et al.  2011.  [Adaptive Subgradient Methods for Online Learning and Stochastic Optimization](http://jmlr.org/papers/v12/duchi11a.html).  JMLR.
 1. Goodfellow, et al.  2016.  [Deep Learning](https://www.deeplearningbook.org/)
 1. Kingma, D. and Ba, J.  2014.  [Adam: A Method for Stochastic Optimization](https://arxiv.org/abs/1412.6980)
 1. Reddi, S. et al.  2018.  [On the Convergence of Adam and Beyond](https://openreview.net/forum?id=ryQu7f-RZ).  ICLR. [Introduces AMSGrad].
 1. [StackExchange: What's the difference between momentum based gradient descent and Nesterov's accelerated gradient descent?](https://stats.stackexchange.com/questions/179915/whats-the-difference-between-momentum-based-gradient-descent-and-nesterovs-acc)
 1. [Source code for pytorch v1.4.0 `torch.optim.sgd`](https://pytorch.org/docs/stable/_modules/torch/optim/sgd.html#SGD.step) -- SGD, momentum, and Nesterov momentum.
 1. [Source code for pytorch v1.4.0 `torch.optim.Adam`](https://pytorch.org/docs/stable/_modules/torch/optim/adam.html#Adam.step)
 1. [Wikipedia article on $R^2$](https://en.wikipedia.org/wiki/Coefficient_of_determination)